In [1]:
import tensorflow as tf
tf.python.control_flow_ops = tf

import os
import pandas as pd
import numpy as np
import cv2
from keras.models import Sequential
from keras.layers import Flatten, Dense, Dropout, \
MaxPooling2D, Conv2D, Lambda, Cropping2D, Convolution2D,\
AveragePooling2D
from keras.callbacks import History,TensorBoard, EarlyStopping, ModelCheckpoint
from sklearn.cross_validation import train_test_split

from copy import deepcopy
from sklearn.utils import shuffle


from generator import generator
from get_images import get_images


Using TensorFlow backend.
/root/anaconda3/envs/carnd-term1/lib/python3.5/site-packages/sklearn/cross_validation.py:44: DeprecationWarning: This module was deprecated in version 0.18 in favor of the model_selection module into which all the refactored classes and functions are moved. Also note that the interface of the new CV iterators are different from that of this module. This module will be removed in 0.20.
  "This module will be removed in 0.20.", DeprecationWarning)


In [2]:
datadirs=['/notebooks/udacity/new_training/map1_backward/',
                 '/notebooks/udacity/new_training/map1_forward/',
                 '/notebooks/udacity/new_training/map1_recovery_backward/',
                 '/notebooks/udacity/new_training/map1_recovery_forward/']#,
                 #'/notebooks/udacity/new_training/map2_forward/',
                 #'/notebooks/udacity/new_training/map2_backward/',
                 #'/notebooks/udacity/new_training/map2_recovery_forward/',
                 #'/notebooks/udacity/new_training/map2_recovery_backward/']

images=get_images(datadirs)

In [3]:
size=(40,80)

def preprocessing_resize(im):
    return cv2.resize(cv2.cvtColor(im, cv2.COLOR_BGR2YUV),(size[1],size[0]))

In [4]:
from car_models import *

In [5]:
grid=[
    {'get_model':modified_lenet, 'correction':0.2, \
       'preprocessing':preprocessing_resize,'optimizer':'adam','gpu':'1','name':'lenet_02_adam'},\
     {'get_model':nvidia_net, 'correction':0.2, \
       'preprocessing':lambda x:x,'optimizer':'adam','gpu':'1','name':'nvidia_net_02_adam'},
      {'get_model':inception, 'correction':0.2, \
       'preprocessing':lambda x:x,'optimizer':'adam','gpu':'1','name':'inception_02_adam'},
     {'get_model':vgg16, 'correction':0.2, \
       'preprocessing':lambda x:x,'optimizer':'adam','gpu':'1','name':'vgg16_02_adam'}
     
     
     ]

In [6]:
import os
import pickle

def train_model(get_model, correction, preprocessing, name, optimizer, gpu):
    import os

    os.environ['CUDA_VISIBLE_DEVICES']=str(gpu)
    
    model=get_model()
    model.compile(loss='mse', optimizer=optimizer, metrics=['mean_squared_error'])
    
    if not os.path.exists('results/logs_%s'%name):
        os.mkdir('results/logs_%s'%name)
    
    
    checkpoint = ModelCheckpoint("results/model_%s.h5" % name, monitor='val_mean_squared_error', verbose=1,
                              save_best_only=True, mode='min')
    early_stop = EarlyStopping(monitor='val_mean_squared_error',\
                               min_delta=0.001, patience=3,
                                verbose=1, mode='min')

    history = History()

    tb=TensorBoard(log_dir='results/logs_%s'%name, histogram_freq=0, write_graph=True, write_images=False)

    train_generator = generator(deepcopy(images), dataset=0, batch_size=128, preprocessing=preprocessing)
    validation_generator = generator(deepcopy(images), dataset=1, batch_size=128, preprocessing=preprocessing)
    test_generator = generator(deepcopy(images), dataset=2, batch_size=128, preprocessing=preprocessing)

    ##todo - nb_epoch=100
    model.fit_generator(train_generator, \
                    samples_per_epoch=len(images[images.dataset==0]),\
                    nb_epoch=100,\
                    verbose=1,\
                    validation_data=validation_generator, \
                    nb_val_samples=len(images[images.dataset==1]),\
                    callbacks=[checkpoint, early_stop,history,tb]\
                   )
    
    f=open('results/history_%s.pk1' % name,'wb')
    pickle.dump(history.history,f,-1)
    f.close()
    
    #realy it's from last iteration - better to load best model here
    res=model.evaluate_generator(test_generator,val_samples=len(images[images.dataset==1]))[0]
    return res

In [ ]:
res=train_model(**grid[1])

Instructions for updating:
Please switch to tf.summary.merge_all.
Epoch 1/100
184926/184926 [==============================] - 221s - loss: 0.0808 - mean_squared_error: 0.0808 - val_loss: 0.1270 - val_mean_squared_error: 0.1270
Epoch 2/100
184926/184926 [==============================] - 222s - loss: 0.0713 - mean_squared_error: 0.0713 - val_loss: 0.1056 - val_mean_squared_error: 0.1056
Epoch 3/100
184926/184926 [==============================] - 222s - loss: 0.0659 - mean_squared_error: 0.0659 - val_loss: 0.1012 - val_mean_squared_error: 0.1012
Epoch 4/100
184926/184926 [==============================] - 223s - loss: 0.0666 - mean_squared_error: 0.0666 - val_loss: 0.0956 - val_mean_squared_error: 0.0956
Epoch 5/100
184926/184926 [==============================] - 223s - loss: 0.0635 - mean_squared_error: 0.0635 - val_loss: 0.0933 - val_mean_squared_error: 0.0933
Epoch 6/100
184926/184926 [==============================] - 224s - loss: 0.0645 - mean_squared_error: 0.0645 - val_loss: 0.

In [37]:
grid2=[{'get_model':nvidia_net, 'correction':0.3, \
       'preprocessing':lambda x:x,'optimizer':'adam','gpu':'0','name':'nvidia_net_03_adam'} 
     
     ]

In [39]:
res3=[train_model(**a) for a in grid2]

Instructions for updating:
Please switch to tf.summary.merge_all.
Epoch 1/100
184926/184926 [==============================] - 222s - loss: 0.0740 - mean_squared_error: 0.0740 - val_loss: 0.1060 - val_mean_squared_error: 0.1060
Epoch 2/100
184926/184926 [==============================] - 224s - loss: 0.0649 - mean_squared_error: 0.0649 - val_loss: 0.1036 - val_mean_squared_error: 0.1036
Epoch 3/100
184926/184926 [==============================] - 222s - loss: 0.0634 - mean_squared_error: 0.0634 - val_loss: 0.0963 - val_mean_squared_error: 0.0963
Epoch 4/100
184926/184926 [==============================] - 222s - loss: 0.0636 - mean_squared_error: 0.0636 - val_loss: 0.1013 - val_mean_squared_error: 0.1013
Epoch 5/100
184926/184926 [==============================] - 222s - loss: 0.0629 - mean_squared_error: 0.0629 - val_loss: 0.1093 - val_mean_squared_error: 0.1093
Epoch 6/100
184926/184926 [==============================] - 222s - loss: 0.0627 - mean_squared_error: 0.0627 - val_loss: 0.

KeyboardInterrupt: 

In [24]:
%%sh

ls results/

logs_lenet_02_adam
logs_nvidia_net_02_adam
model_lenet_02_adam.h5


In [9]:
res

[0.090735534215862446, 0.081087654837275758]

In [17]:
model = Sequential([
    Conv2D(32, 3, 3, input_shape=(16, 32, 1), border_mode='same', activation='relu'),
    Conv2D(64, 3, 3, border_mode='same', activation='relu'),
    Dropout(0.5),
    Conv2D(128, 3, 3, border_mode='same', activation='relu'),
    Conv2D(256, 3, 3, border_mode='same', activation='relu'),
    Dropout(0.5),
    Flatten(),
    Dense(1024, activation='relu'),
    Dense(512, activation='relu'),
    Dense(128, activation='relu'),
    Dense(1, name='output', activation='tanh'),
])

In [35]:
size=(16,32)

def preprocessing_resize(im):
    return cv2.resize(cv2.cvtColor(im, cv2.COLOR_BGR2GRAY),(size[1],size[0])).reshape(16,32,1)

model.compile(loss='mse', optimizer='adagrad', metrics=['mean_squared_error'])



checkpoint = ModelCheckpoint("test.h5" , monitor='val_mean_squared_error', verbose=1,
                          save_best_only=True, mode='min')
early_stop = EarlyStopping(monitor='val_mean_squared_error',\
                           min_delta=0.001, patience=3,
                            verbose=1, mode='min')

history = History()


train_generator = generator(deepcopy(images), dataset=0, batch_size=128, preprocessing=preprocessing_resize)
validation_generator = generator(deepcopy(images), dataset=1, batch_size=128, preprocessing=preprocessing_resize)
test_generator = generator(deepcopy(images), dataset=2, batch_size=128, preprocessing=preprocessing_resize)

##todo - nb_epoch=100
model.fit_generator(train_generator, \
                samples_per_epoch=len(images[images.dataset==0]),\
                nb_epoch=100,\
                verbose=1,\
                validation_data=validation_generator, \
                nb_val_samples=len(images[images.dataset==1]),\
                callbacks=[checkpoint, early_stop,history]\
               )

Epoch 1/100
184926/184926 [==============================] - 175s - loss: 1.1667 - mean_squared_error: 1.1667 - val_loss: 1.1721 - val_mean_squared_error: 1.1721
Epoch 2/100
184926/184926 [==============================] - 171s - loss: 1.1666 - mean_squared_error: 1.1666 - val_loss: 1.1721 - val_mean_squared_error: 1.1721
Epoch 3/100
184926/184926 [==============================] - 171s - loss: 1.1666 - mean_squared_error: 1.1666 - val_loss: 1.1721 - val_mean_squared_error: 1.1721
Epoch 4/100
184926/184926 [==============================] - 170s - loss: 1.1666 - mean_squared_error: 1.1666 - val_loss: 1.1721 - val_mean_squared_error: 1.1721
Epoch 5/100
 14976/184926 [=>............................] - ETA: 115s - loss: 1.0558 - mean_squared_error: 1.0558

KeyboardInterrupt: 

In [21]:
im=cv2.imread(images.values[0][0])

In [30]:
size=(16,32)

def preprocessing_resize(im):
    return cv2.resize(cv2.cvtColor(im, cv2.COLOR_BGR2GRAY),(size[1],size[0]))

tmp=preprocessing_resize(im)

In [33]:
tmp.reshape((16,32,1)).shape

(16, 32, 1)

In [34]:
im.shape

(160, 320, 3)